# Audio Sample File Generator
This is meant to emulate something like this test record: https://ortofon.com/products/ortofon-test-record

Ideally it provides a consistent source to dial in your laser settings after running the Audio to SVG notebook

In [1]:
# Install a pip package in the current Jupyter kernel
import sys
!{sys.executable} -m pip install python-sound

In [2]:
import numpy as np
from scipy.io.wavfile import write
import io
import array

import IPython

In [3]:
# Frequency in Hz
start_frequency = 800 
end_frequency = 50000

# How long should the total sweep be in seconds
total_duration = 28

# Additional parameters
sample_rate = 44100
frequency_step = 99 # how to change the frequency over time

# Output variables
filename = "frequency_sweep.wav"

In [4]:
# Some precalcuation before we start
tone_duration = total_duration / ((end_frequency - start_frequency) / frequency_step)
frequencies = np.arange(start_frequency, end_frequency + 1, frequency_step)
total_iterations = len(frequencies)

print(f"Using a tone_duration of {tone_duration} with {total_iterations} total_iterations")

Using a tone_duration of 0.05634146341463414 with 497 total_iterations


In [5]:
# helper method for generating the tone
def generate_tone(frequency, duration):
    t = np.linspace(0, duration, int(sample_rate * duration), False)
    tone = np.sin(2 * np.pi * frequency * t)
    return (tone * 32767).astype(np.int16)

In [6]:
# loop through all the steps of the sweep and write them to a buffer

sweep_io = io.BytesIO()
for i, frequency in enumerate(frequencies):
    tone = generate_tone(frequency, tone_duration)
    sweep_io.write(tone)


In [7]:
# Get the data for the first channel out of the data
channel_1 = np.frombuffer(sweep_io.getvalue(), np.int16)
print(f'Channel 1: {channel_1.shape}')

# Create a second channel of all zeros
channel_2 = np.zeros(len(channel_1), dtype=np.int16)
print(f'Channel 2: {channel_2.shape}')

# Create our 2D dataset for 2 channel export (The Audio to SVG script doesn't support single channel)
data = np.column_stack((channel_1, channel_2))
# data = channel_1[..., np.newaxis]
# print(data.shape)

# # Add our second channel that is all zeros
# # data[:,:,1] = np.zeros(len(channel_1), dtype=np.int16)
# data.resize(len(channel_1), len(channel_1))
print(f'Data: {data.shape}')

Channel 1: (1234548,)
Channel 2: (1234548,)
Data: (1234548, 2)


In [8]:
# Let's save our wav file
write(filename, sample_rate, data)

In [9]:
# Play the output file
IPython.display.Audio(filename)